In [44]:
from langchain.document_loaders import UnstructuredExcelLoader
from langchain.indexes import VectorstoreIndexCreator
from langchain.chains import RetrievalQA
from langchain.llms import OpenAI
import os
import openpyxl
import json
from combine_db import make_database

import sys
sys.path.append('../config.py')
from config import OPENAI_API_KEY

In [45]:
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY


In [46]:
if not os.path.exists("excel/database.xlsx"):
    make_database()

In [47]:
workbook = openpyxl.load_workbook("excel/responses.xlsx")
worksheet = workbook.active

In [48]:
loader = UnstructuredExcelLoader(
    "excel/database.xlsx",
    mode="elements",
)
docs = loader.load()
print(docs)

[Document(lc_kwargs={'page_content': '\n  \n    \n      Amit Sheth\n      Prof. Sheth calls himself a ‘tinkerer’; graduated in Electrical & Electronics Engineering from BITS Pilani, did his Masters in Product Design from National Institute of Design, Ahmedabad; and an M.Phil. from Industrial Design Centre, IITB, Mumbai. Prof. Sheth has been a design practitioner for the past three decades as well as a design educator. \\nDuring his 30 years as a design consultant, Prof. Sheth’s firm MIND’s EYE DESIGN Pvt Ltd has provided design services in the areas of Product Design, Signage & Wayfinding Design, Exhibition Design, Corporate Branding, Interiors and Architecture. He was instrumental in setting up the Design Institute for Nirma University and was Professor & Head of the Department. Post that he was Dean of Advancement and a Professor at Anant National University, Ahmedabad, and Adjunct Professor at NRTI (National Rail & Transportation Institute, Vadodara) as well as IIT Gandhinagar.\n   

In [49]:
# Create an index using the loaded documents
index_creator = VectorstoreIndexCreator()
docsearch = index_creator.from_loaders([loader])

In [50]:
# Create a question-answering chain using the index
chain = RetrievalQA.from_chain_type(
    llm=OpenAI(temperature=0),
    chain_type="stuff",
    retriever=docsearch.vectorstore.as_retriever(),
    input_key="question",
)

In [51]:
def answer_question(field_of_interest):
    query = f"""
    I have given you a list of my university's faculty members and founder, along with their backgrounds. I want you to take your time to understand and remember this information. I will give you an area of interest and you need to tell me which faculty members and founders have the most relevant experience in that area, so that I can go and speak to them regarding the same. Give me the relevant names, along with your reasoning as to why they are the ideal people to speak to. Your output should be in a JSON format, with the keys 'source' (faculty or founder), 'name' and 'reasoning'. An example is given below in double backticks: 
    ``
    [
    {{
        "source": "faculty",
        "name": "Dr A",
        "reasoning": ""
    }},
    {{
        "source": "founder",
        "name": "Mr B",
        "reasoning": ""
    }}
    ]
    ``
    Output only the JSON response, without the backticks.

    My first prompt is the following, enclosed within triple backticks:
    ```
    I am interested in {field_of_interest}.
    ```
    """
    response = chain({"question": query})
    print(response['result'])
    response = json.loads(response['result'])
    for i in response:
        worksheet.append([field_of_interest, i['name'], i['reasoning']])

In [52]:
answer_question("design thinking and innovation")


[
    {
        "source": "faculty",
        "name": "Dr Srikant Srinivasan",
        "reasoning": "Specializes in Engineering Education which includes design thinking and innovation."
    },
    {
        "source": "faculty",
        "name": "Dr Shashikant Pawar",
        "reasoning": "Specializes in Bio-inspired Energy-efficient and Sustainable Systems which includes design thinking and innovation."
    },
    {
        "source": "founder",
        "name": "Dr Nitin Upadhyaya",
        "reasoning": "Works towards developing practical solutions for senior care using a combination of analytical methods, technology and field work which includes design thinking and innovation."
    }
]


In [53]:
answer_question("philosophy")


[
    {
        "source": "faculty",
        "name": "Dr. Chaitanya Lekshmi Indira",
        "reasoning": "Dr. Chaitanya Lekshmi Indira specializes in philosophy."
    }
]


In [54]:
answer_question("applied mathematics")


[
    {
        "source": "faculty",
        "name": "Dr. Nitin Upadhyaya",
        "reasoning": "His research interests lie at the intersection of physics, behavioral science and applied math."
    }
]


In [55]:
answer_question("IOT systems")


[
    {
        "source": "faculty",
        "name": "Dr. Shashikant Pawar",
        "reasoning": "Specializes in Fluid Mechanics and Heat Transfer, which are relevant to IOT systems."
    },
    {
        "source": "faculty",
        "name": "Dr. Nitin Upadhyaya",
        "reasoning": "Research interests lie at the intersection of physics, behavioral science and applied math, which are relevant to IOT systems."
    }
]


In [56]:
answer_question("Embedded systems and machine learning")


[
    {
        "source": "faculty",
        "name": "Dr. Srikant Srinivasan",
        "reasoning": "He specializes in Fluid Mechanics and Heat Transfer, which are related to Embedded systems and machine learning."
    },
    {
        "source": "faculty",
        "name": "Dr. Shashikant Pawar",
        "reasoning": "He specializes in Bio-inspired Energy-efficient and Sustainable Systems, which are related to Embedded systems and machine learning."
    },
    {
        "source": "faculty",
        "name": "Dr. Chaitanya Lekshmi Indira",
        "reasoning": "She specializes in Fluid Dynamics and Heat Transfer, which are related to Embedded systems and machine learning."
    },
    {
        "source": "faculty",
        "name": "Dr. Shashank Tamaskar",
        "reasoning": "He specializes in Buoyancy driven (environmental) turbulent flows, which are related to Embedded systems and machine learning."
    }
]


In [57]:
answer_question("Thermodynamics")


[
    {
        "source": "faculty",
        "name": "Dr. Shashikant Pawar",
        "reasoning": "Specializes in Fluid Mechanics and Heat Transfer"
    },
    {
        "source": "faculty",
        "name": "Dr. Nitin Upadhyaya",
        "reasoning": "Research interests include Fluid Dynamics and Heat Transfer"
    }
]


In [58]:
answer_question("cyber security")


[
    {
        "source": "faculty",
        "name": "Dr Srikant Srinivasan",
        "reasoning": "Specializes in Fluid Mechanics and Heat Transfer"
    },
    {
        "source": "faculty",
        "name": "Dr Shashikant Pawar",
        "reasoning": "Specializes in Fluid Dynamics and Heat Transfer"
    },
    {
        "source": "faculty",
        "name": "Dr Chaitanya Lekshmi Indira",
        "reasoning": "No relevant experience"
    },
    {
        "source": "faculty",
        "name": "Dr Shashank Tamaskar",
        "reasoning": "No relevant experience"
    }
]


In [59]:
answer_question("micro and macro economics")


[
    {
        "source": "faculty",
        "name": "Dr. Shashikant Pawar",
        "reasoning": "He specializes in Fluid Mechanics and Heat Transfer, which includes microclimate studies."
    },
    {
        "source": "faculty",
        "name": "Dr. Srikant Srinivasan",
        "reasoning": "No specific information is given about his background, so he may have experience in micro and macro economics."
    },
    {
        "source": "faculty",
        "name": "Dr. Chaitanya Lekshmi Indira",
        "reasoning": "No specific information is given about her background, so she may have experience in micro and macro economics."
    },
    {
        "source": "faculty",
        "name": "Dr. Shashank Tamaskar",
        "reasoning": "No specific information is given about his background, so he may have experience in micro and macro economics."
    }
]


In [60]:
answer_question("biology, preferably genetics")


[
    {
        "source": "faculty",
        "name": "Dr. Chaitanya Lekshmi Indira",
        "reasoning": "Specializes in genetics"
    },
    {
        "source": "faculty",
        "name": "Dr. Shashikant Pawar",
        "reasoning": "Research interests include bio-inspired energy-efficient and sustainable systems"
    }
]


In [61]:
# workbook.save("responses.xlsx")